<a href="https://colab.research.google.com/github/breathofthe/Text-Mining/blob/main/LDA_model_(newsgroup_data).ipynb" target="_parent"><img src="https://colab.research.google.com/assets/colab-badge.svg" alt="Open In Colab"/></a>

### Importing 20 newsgroups data

In [3]:
from sklearn.datasets import fetch_20newsgroups

In [2]:
newsgroups_train = fetch_20newsgroups(subset='train')
newsgroups_train.target_names

['alt.atheism',
 'comp.graphics',
 'comp.os.ms-windows.misc',
 'comp.sys.ibm.pc.hardware',
 'comp.sys.mac.hardware',
 'comp.windows.x',
 'misc.forsale',
 'rec.autos',
 'rec.motorcycles',
 'rec.sport.baseball',
 'rec.sport.hockey',
 'sci.crypt',
 'sci.electronics',
 'sci.med',
 'sci.space',
 'soc.religion.christian',
 'talk.politics.guns',
 'talk.politics.mideast',
 'talk.politics.misc',
 'talk.religion.misc']

#### 분석 대상 주제 선택
20개의 주제 중 각자 5개의 주제를 선택하여 "categories" 리스트를 작성하고 이 리스트를 이용하여 "newsgroups_train" 데이터의 일부만 불러와서 와서 "newsgroups_train"라는 이름으로 저장합니다.
 `comp.sys.ibm.pc.hardware`, `misc.forsale`, `rec.sport.baseball`, `sci.space`, `talk.politics.guns`를 선택하여 다음과 같은 명령문을 작성하겠습니다

In [4]:
categories = ["comp.sys.ibm.pc.hardware", "misc.forsale", "rec.sport.baseball", "sci.space", "talk.politics.guns"]
newsgroups_train = fetch_20newsgroups(subset='train', categories=categories)

In [5]:
dir(newsgroups_train)

['DESCR', 'data', 'filenames', 'target', 'target_names']

In [6]:
newsgroups_train.data[0]

"From: martimer@jaguar.WPI.EDU (the random one...)\nSubject: Re: VHS movie for sale\nOrganization: Worcester Polytechnic Institute\nLines: 10\nNNTP-Posting-Host: jaguar.wpi.edu\n\nIn article <1993Apr19.211400.1@hirama.hiram.edu> koutd@hirama.hiram.edu (DOUGLAS KOU) writes:\n>VHS movie for sale.\n>\n>Dance with Wovies\t($12.00)\n\t    ^^^^^^ what the  hell ios a 'wovie' ?? (wovy (sp))??\n \n-- \n \t\tFrom there to here, from here to there,\n \t\t\tfunny things are everywhere \t     Dr. Suess\n..jonathan Sawitsky       'some random wierdo'         martimer@wpi.wpi.edu...\n"

In [7]:
newsgroups_train.filenames[0]

'/root/scikit_learn_data/20news_home/20news-bydate-train/misc.forsale/76052'

In [8]:
newsgroups_train.target[0]

1

### Preprocessing
다음과 같이 기본적인 전처리 과정을 진행합니다.

In [9]:
import re
import nltk
nltk.download('stopwords')
nltk.download('punkt')
nltk.download('wordnet')
nltk.download('averaged_perceptron_tagger')
nltk.download('omw-1.4')
from nltk.stem import WordNetLemmatizer
wnl = WordNetLemmatizer()
from nltk.corpus import stopwords
stopwordslist = stopwords.words("english")

[nltk_data] Downloading package stopwords to /root/nltk_data...
[nltk_data]   Unzipping corpora/stopwords.zip.
[nltk_data] Downloading package punkt to /root/nltk_data...
[nltk_data]   Unzipping tokenizers/punkt.zip.
[nltk_data] Downloading package wordnet to /root/nltk_data...
[nltk_data] Downloading package averaged_perceptron_tagger to
[nltk_data]     /root/nltk_data...
[nltk_data]   Unzipping taggers/averaged_perceptron_tagger.zip.
[nltk_data] Downloading package omw-1.4 to /root/nltk_data...


In [10]:
# POS fetching
def get_wnpos(tag):
    if tag.startswith('J'):
        return 'a'
    elif tag.startswith('V'):
        return 'v'
    elif tag.startswith('N'):
        return 'n'
    elif tag.startswith('R'):
        return 'r'
    else:
        return None

In [11]:
# tokenization
from nltk.stem import WordNetLemmatizer
wnl = WordNetLemmatizer()
stop_words = stopwords.words("english")
def my_tokenizer(text):
    words = nltk.word_tokenize(text)
    tokens = [word.lower() for word in words]
    tokens = nltk.pos_tag(tokens)
    tokens = [wnl.lemmatize(word, get_wnpos(tag)) if get_wnpos(tag) is not None else word for word, tag in tokens]
    tokens = [re.sub("\d+", "", w) for w in tokens]
    tokens = [re.sub(r"[^\w\-\']","",w) for w in tokens]
    tokens = [w for w in tokens if w not in stop_words]
    tokens = list(filter(None, tokens))
    return tokens
news_data = newsgroups_train.data
news_docs = [my_tokenizer(news_data[i]) for i in range(len(news_data))]
news_docs

[['martimer',
  'jaguarwpiedu',
  'random',
  'one',
  'subject',
  'vhs',
  'movie',
  'sale',
  'organization',
  'worcester',
  'polytechnic',
  'institute',
  'line',
  'nntp-posting-host',
  'jaguarwpiedu',
  'article',
  'apr',
  'hiramahiramedu',
  'koutd',
  'hiramahiramedu',
  'douglas',
  'kou',
  'write',
  'vhs',
  'movie',
  'sale',
  'dance',
  'wovies',
  'hell',
  'ios',
  "'wovie",
  "'",
  'wovy',
  'sp',
  '--',
  'funny',
  'thing',
  'everywhere',
  'dr',
  'sue',
  'jonathan',
  'sawitsky',
  "'some",
  'random',
  'wierdo',
  "'",
  'martimer',
  'wpiwpiedu'],
 ['paul',
  'csdcsduwmedu',
  'paul',
  'r',
  'krueger',
  'subject',
  'brewer',
  'bullpen',
  'rock',
  'organization',
  'computing',
  'service',
  'division',
  'university',
  'wisconsin',
  '-',
  'milwaukee',
  'line',
  'distribution',
  'world',
  'nntp-posting-host',
  'originator',
  'paul',
  'csdcsduwmedu',
  'second',
  'straight',
  'game',
  'california',
  'score',
  'ton',
  'late',
  '

In [12]:
print(news_docs[0])

['martimer', 'jaguarwpiedu', 'random', 'one', 'subject', 'vhs', 'movie', 'sale', 'organization', 'worcester', 'polytechnic', 'institute', 'line', 'nntp-posting-host', 'jaguarwpiedu', 'article', 'apr', 'hiramahiramedu', 'koutd', 'hiramahiramedu', 'douglas', 'kou', 'write', 'vhs', 'movie', 'sale', 'dance', 'wovies', 'hell', 'ios', "'wovie", "'", 'wovy', 'sp', '--', 'funny', 'thing', 'everywhere', 'dr', 'sue', 'jonathan', 'sawitsky', "'some", 'random', 'wierdo', "'", 'martimer', 'wpiwpiedu']


In [13]:
len(news_docs)

2911

# DTM

CountVectorizer() 함수를 이용하여 문서-단어행렬을 작성할 것이며

* 단, 지나치게 빈번하게 또는 지나치게 드물게 등장하는 단어들을 제거하기 위해 문서빈도가 0.02 이상 0.95 이하인 단어들만으로 문서-단어행렬을 생성하겠습니다.

* 문서-단어행렬은 pandas 데이터프레임 형태로 표현하고 열 인덱스는 각 단어가 되도록 할 것입니다.

* 생성된 문서-단어행렬의 행과 열의 개수를 확인해보겠습니다.

In [14]:
from sklearn.feature_extraction.text import CountVectorizer
import pandas as pd

# CountVectorizer 설정: 문서빈도가 0.02 이상 0.95 이하인 단어들만 포함
vectorizer = CountVectorizer(tokenizer=my_tokenizer, min_df=0.02, max_df=0.95)

# 문서-단어 행렬 생성
X = vectorizer.fit_transform(newsgroups_train.data)

# Pandas 데이터프레임으로 변환
df = pd.DataFrame(X.toarray(), columns=vectorizer.get_feature_names_out())

# 행과 열의 개수 확인
print(f"Number of rows: {df.shape[0]}")
print(f"Number of columns: {df.shape[1]}")


/usr/local/lib/python3.10/dist-packages/sklearn/feature_extraction/text.py:528: UserWarning: The parameter 'token_pattern' will not be used since 'tokenizer' is not None'
  warnings.warn(


Number of rows: 2911
Number of columns: 878


In [15]:
df.head()

'  ''  'd  'll  'm  're  's  've  -  --  ...  x-newsreader  yankee  yeah  \
0  2   0   0    0   0    0   0    0  0   1  ...             0       0     0   
1  0   0   0    0   0    1   6    0  5   1  ...             0       0     0   
2  1   1   0    0   0    0   0    0  1   2  ...             0       0     0   
3  0   8   0    1   0    0   2    0  1   0  ...             0       0     0   
4  0   0   0    0   0    0   0    0  1   1  ...             0       0     0   

   year  yes  yesterday  yet  york  young  zootorontoedu  
0     0    0          0    0     0      0              0  
1     2    0          3    0     0      0              0  
2     0    0          0    0     0      0              0  
3     0    0          0    0     0      0              0  
4     0    0          0    0     0      0              0  

[5 rows x 878 columns]

**table을 보면 열 인덱스가 각각의 단어가 되었음을 알 수 있습니다.**


두 개의 서로 다른 문서를 선택하여 코사인 유사도를 평가 할 것입니다.

In [16]:
from sklearn.metrics.pairwise import cosine_similarity

In [17]:
def cos(matrix):
    # 코사인 유사도 계산
    cosine_sim = cosine_similarity(matrix)
    return cosine_sim

In [18]:
# 두 문서의 인덱스 선택
index1 = 0
index2 = 1

# 코사인 유사도 계산
cosine_sim = cos(X)

# 선택한 두 문서의 코사인 유사도 출력
print(cosine_sim[index1, index2])

0.04639051998342823


**0번 문서와 1번문서의 유사도를 계산하였습니다**

# TF-IDF DTM

NumPy의 기본함수들만 이용하여 TF-IDF 방식의 문서-단어행렬을 작성하 겠습니다.

* 위에서 생성한 문서-단어행렬을 이용하여 각 단어의 문서빈도(df)를 확인해 보겠습니다.

* 단어빈도는 단어의 출현빈도를 이용하고 log(N/df)를 곱하여 TF-IDF 방식 DTM을 생성할 것입니다.(단, N은 전체 문서의 수)

In [19]:
import numpy as np

In [20]:
# 문서-단어 행렬 생성
X = vectorizer.fit_transform(newsgroups_train.data).toarray()

# 전체 문서의 수
N = X.shape[0]

# 각 단어의 문서 빈도 계산
df = np.sum(X > 0, axis=0)

# TF 계산
tf = X

# IDF 계산
idf = np.log(N / df)

# IDF의 차원을 맞추기 위해 reshape
idf = idf.reshape(1, -1)

# TF-IDF 계산
tfidf = tf * idf

# 결과 확인
print("TF-IDF 행렬 SHAPE:", tfidf.shape)
print("TF-IDF 행렬의 첫번째 문서:", tfidf[0])

/usr/local/lib/python3.10/dist-packages/sklearn/feature_extraction/text.py:528: UserWarning: The parameter 'token_pattern' will not be used since 'tokenizer' is not None'
  warnings.warn(


TF-IDF 행렬 SHAPE: (2911, 878)
TF-IDF 행렬의 첫번째 문서: [3.49943055 0.         0.         0.         0.         0.
 0.         0.         0.         0.56288461 0.         0.
 0.         0.         0.         0.         0.         0.
 0.         0.         0.         0.         0.         0.
 0.         0.         0.         0.         0.         0.
 0.         0.         0.         0.         0.         0.
 0.         0.         0.         0.         0.         0.
 0.         0.         0.         0.         0.         0.
 0.         0.         0.         0.         0.         0.
 0.         0.         0.         1.51166364 0.         0.
 0.         0.         0.         0.95160291 0.         0.
 0.         0.         0.         0.         0.         0.
 0.         0.         0.         0.         0.         0.
 0.         0.         0.         0.         0.         0.
 0.         0.         0.         0.         0.         0.
 0.         0.         0.         0.         0.         0.
 0.     

**기존행렬과 비교하기**

In [21]:
# 첫 번째 문서의 기존 문서-단어 행렬 값을 출력

print("기존 문서 단어행렬의 첫번째 문서:", X[0])

기존 문서 단어행렬의 첫번째 문서: [2 0 0 0 0 0 0 0 0 1 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0
 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 1 0 0 0 0 0 1 0 0 0 0 0 0 0 0 0 0
 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0
 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0
 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0
 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0
 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0
 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0
 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0
 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 1 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0
 0 0 0 0 0 0 0 0 0 0 0 0 0 0 1 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0
 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0
 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0
 0 0 

**기존의 문서단어행렬과 비교 해봤을때 가중치를 곱하여 잘 처리가 되었음을 알 수 있습니다.**

# LDA

gensim 딕셔너리를 생성합니다.



* filter_extremes() 메서드를 이용하여 문서빈도가 0.02 미만인 단어들은 제거할 것

In [22]:
# 텍스트 데이터를 딕셔너리로 전환
from gensim import corpora
dictionary = corpora.Dictionary(news_docs)
print(dictionary)

Dictionary<35601 unique tokens: ["'", "'some", "'wovie", '--', 'apr']...>


In [23]:
# 딕셔너리에 적용할 수 있는 메서드와 애트리뷰트 확인
dir(dictionary)

['__abstractmethods__',
 '__class__',
 '__class_getitem__',
 '__contains__',
 '__delattr__',
 '__dict__',
 '__dir__',
 '__doc__',
 '__eq__',
 '__format__',
 '__ge__',
 '__getattribute__',
 '__getitem__',
 '__gt__',
 '__hash__',
 '__init__',
 '__init_subclass__',
 '__iter__',
 '__le__',
 '__len__',
 '__lt__',
 '__module__',
 '__ne__',
 '__new__',
 '__reduce__',
 '__reduce_ex__',
 '__repr__',
 '__reversed__',
 '__setattr__',
 '__sizeof__',
 '__slots__',
 '__str__',
 '__subclasshook__',
 '__weakref__',
 '_abc_impl',
 '_adapt_by_suffix',
 '_load_specials',
 '_save_specials',
 '_smart_save',
 'add_documents',
 'add_lifecycle_event',
 'cfs',
 'compactify',
 'dfs',
 'doc2bow',
 'doc2idx',
 'filter_extremes',
 'filter_n_most_frequent',
 'filter_tokens',
 'from_corpus',
 'from_documents',
 'get',
 'id2token',
 'items',
 'iteritems',
 'iterkeys',
 'itervalues',
 'keys',
 'lifecycle_events',
 'load',
 'load_from_text',
 'merge_with',
 'most_common',
 'num_docs',
 'num_nnz',
 'num_pos',
 'patch_wi

In [24]:
# 딕셔너리의 키
dictionary.keys()

[0,
 1,
 2,
 3,
 4,
 5,
 6,
 7,
 8,
 9,
 10,
 11,
 12,
 13,
 14,
 15,
 16,
 17,
 18,
 19,
 20,
 21,
 22,
 23,
 24,
 25,
 26,
 27,
 28,
 29,
 30,
 31,
 32,
 33,
 34,
 35,
 36,
 37,
 38,
 39,
 40,
 41,
 42,
 43,
 44,
 45,
 46,
 47,
 48,
 49,
 50,
 51,
 52,
 53,
 54,
 55,
 56,
 57,
 58,
 59,
 60,
 61,
 62,
 63,
 64,
 65,
 66,
 67,
 68,
 69,
 70,
 71,
 72,
 73,
 74,
 75,
 76,
 77,
 78,
 79,
 80,
 81,
 82,
 83,
 84,
 85,
 86,
 87,
 88,
 89,
 90,
 91,
 92,
 93,
 94,
 95,
 96,
 97,
 98,
 99,
 100,
 101,
 102,
 103,
 104,
 105,
 106,
 107,
 108,
 109,
 110,
 111,
 112,
 113,
 114,
 115,
 116,
 117,
 118,
 119,
 120,
 121,
 122,
 123,
 124,
 125,
 126,
 127,
 128,
 129,
 130,
 131,
 132,
 133,
 134,
 135,
 136,
 137,
 138,
 139,
 140,
 141,
 142,
 143,
 144,
 145,
 146,
 147,
 148,
 149,
 150,
 151,
 152,
 153,
 154,
 155,
 156,
 157,
 158,
 159,
 160,
 161,
 162,
 163,
 164,
 165,
 166,
 167,
 168,
 169,
 170,
 171,
 172,
 173,
 174,
 175,
 176,
 177,
 178,
 179,
 180,
 181,
 182,
 183,
 184,


**키값을 이용하여 단어를 선택하는 예시**

In [25]:
dictionary.get(2)

"'wovie"

In [26]:
# 토큰:단어 인덱스 딕셔너리
dictionary.token2id

{"'": 0,
 "'some": 1,
 "'wovie": 2,
 '--': 3,
 'apr': 4,
 'article': 5,
 'dance': 6,
 'douglas': 7,
 'dr': 8,
 'everywhere': 9,
 'funny': 10,
 'hell': 11,
 'hiramahiramedu': 12,
 'institute': 13,
 'ios': 14,
 'jaguarwpiedu': 15,
 'jonathan': 16,
 'kou': 17,
 'koutd': 18,
 'line': 19,
 'martimer': 20,
 'movie': 21,
 'nntp-posting-host': 22,
 'one': 23,
 'organization': 24,
 'polytechnic': 25,
 'random': 26,
 'sale': 27,
 'sawitsky': 28,
 'sp': 29,
 'subject': 30,
 'sue': 31,
 'thing': 32,
 'vhs': 33,
 'wierdo': 34,
 'worcester': 35,
 'wovies': 36,
 'wovy': 37,
 'wpiwpiedu': 38,
 'write': 39,
 "'re": 40,
 "'s": 41,
 '-': 42,
 'alright': 43,
 'another': 44,
 'around': 45,
 'austin': 46,
 'average': 47,
 'bad': 48,
 'bat': 49,
 'best': 50,
 'big': 51,
 'brewer': 52,
 'brewhas': 53,
 'bullpen': 54,
 'california': 55,
 'cancel': 56,
 'come': 57,
 'computing': 58,
 'crush': 59,
 'csdcsduwmedu': 60,
 'defense': 61,
 'deficit': 62,
 'distribution': 63,
 'division': 64,
 'doran': 65,
 'early': 6

In [27]:
# 문서의 도수분포표를 단어 인덱스-단어 출현 빈도의 튜플로 표현
dictionary.doc2bow(news_docs[0])

[(0, 2),
 (1, 1),
 (2, 1),
 (3, 1),
 (4, 1),
 (5, 1),
 (6, 1),
 (7, 1),
 (8, 1),
 (9, 1),
 (10, 1),
 (11, 1),
 (12, 2),
 (13, 1),
 (14, 1),
 (15, 2),
 (16, 1),
 (17, 1),
 (18, 1),
 (19, 1),
 (20, 2),
 (21, 2),
 (22, 1),
 (23, 1),
 (24, 1),
 (25, 1),
 (26, 2),
 (27, 2),
 (28, 1),
 (29, 1),
 (30, 1),
 (31, 1),
 (32, 1),
 (33, 2),
 (34, 1),
 (35, 1),
 (36, 1),
 (37, 1),
 (38, 1),
 (39, 1)]

**filtering**

In [28]:
# 총 문서 수
total_docs = len(news_docs)

# 문서 빈도가 0.02 미만인 단어를 제거하기 위한 no_below 값 계산
no_below = max(1, int(total_docs * 0.02))

# 딕셔너리 객체 생성
dictionary = corpora.Dictionary(news_docs)

# 빈도 필터링 적용
dictionary.filter_extremes(no_below=no_below, keep_n=100000, keep_tokens=None)

# 필터링 후 딕셔너리 출력
print(dictionary)

# 모든 문서에 대해 BoW 도수분포표를 생성
corpus = [dictionary.doc2bow(text) for text in news_docs]

# 생성된 corpus 출력
for doc in corpus:
    print(doc)

Dictionary<897 unique tokens: ["'", 'apr', 'article', 'hell', 'institute']...>
[(0, 2), (1, 1), (2, 1), (3, 1), (4, 1), (5, 1), (6, 1), (7, 2), (8, 1), (9, 1)]
[(5, 1), (8, 1), (10, 1), (11, 6), (12, 1), (13, 2), (14, 3), (15, 1), (16, 1), (17, 1), (18, 1), (19, 1), (20, 2), (21, 2), (22, 1), (23, 1), (24, 1), (25, 1), (26, 1), (27, 1), (28, 1), (29, 4), (30, 1), (31, 2), (32, 1), (33, 1), (34, 1), (35, 1), (36, 1), (37, 2), (38, 1), (39, 1), (40, 1), (41, 2), (42, 1), (43, 1), (44, 2), (45, 1), (46, 1), (47, 1), (48, 2), (49, 1), (50, 3), (51, 2), (52, 1), (53, 1), (54, 3), (55, 2), (56, 2), (57, 1), (58, 1), (59, 1), (60, 2), (61, 1), (62, 1), (63, 1), (64, 1), (65, 1), (66, 2), (67, 1), (68, 1), (69, 1), (70, 1), (71, 1), (72, 3), (73, 3), (74, 3), (75, 1), (76, 1), (77, 1), (78, 1), (79, 3), (80, 1), (81, 2), (82, 3)]
[(0, 1), (2, 1), (6, 1), (8, 2), (9, 2), (30, 1), (42, 1), (48, 2), (49, 1), (63, 1), (69, 1), (79, 1), (83, 1), (84, 1), (85, 1), (86, 1), (87, 5), (88, 1), (89, 1),

다음과 같은 파라미터 값을 이용하여 "20 newsgropu data"에 대한 LDA 모형을 생성하겠습니다.

생성된 모형의 모수 alpha와 beta 값을 확인하고 beta 행렬의 의미를 파악해보겠습니다.

In [29]:
from sklearn.datasets import fetch_20newsgroups
from sklearn.feature_extraction.text import CountVectorizer
from gensim import corpora
import gensim



In [30]:
# 파라미터 값 지정
num_topics = 10
chunksize = 200
passes = 20
iterations = 400
eval_every = 10

In [31]:
# LDA 모델 생성 및 학습
lda_model = gensim.models.LdaModel(
    corpus=corpus,
    id2word=dictionary,
    num_topics=num_topics,
    chunksize=chunksize,
    passes=passes,
    iterations=iterations,
    eval_every=eval_every
)

# 각 주제 출력
for idx, topic in lda_model.print_topics(-1):
    print(f"Topic: {idx} \nWords: {topic}\n")

Topic: 0 
Words: 0.025*"n't" + 0.023*"fire" + 0.023*"would" + 0.017*"people" + 0.016*"''" + 0.015*"write" + 0.014*"police" + 0.014*"believe" + 0.013*"say" + 0.012*"government"

Topic: 1 
Words: 0.045*"file" + 0.027*"university" + 0.025*"please" + 0.025*"nntp-posting-host" + 0.021*"thanks" + 0.017*"tape" + 0.016*"distribution" + 0.015*"address" + 0.015*"send" + 0.014*"email"

Topic: 2 
Words: 0.039*"n't" + 0.034*"'s" + 0.021*"get" + 0.018*"good" + 0.017*"write" + 0.017*"think" + 0.016*"article" + 0.015*"like" + 0.015*"year" + 0.014*"would"

Topic: 3 
Words: 0.079*"gun" + 0.054*"''" + 0.037*"weapon" + 0.033*"state" + 0.026*"law" + 0.026*"firearm" + 0.023*"right" + 0.021*"control" + 0.020*"use" + 0.018*"crime"

Topic: 4 
Words: 0.084*"''" + 0.036*"sale" + 0.029*"'" + 0.026*"e" + 0.023*"r" + 0.023*"offer" + 0.023*"b" + 0.022*"include" + 0.021*"j" + 0.021*"k"

Topic: 5 
Words: 0.055*"drive" + 0.029*"card" + 0.027*"use" + 0.019*"disk" + 0.019*"system" + 0.018*"scsi" + 0.017*"controller" + 0.

**beta는 각 주제에 대한 확률분포를 말하며 예시로 첫번째 주제에 대해 각 단어가 나타날 확률을 출력해보겠습니다.**

In [32]:
# alpha와 beta 계산
alpha = lda_model.alpha
beta = lda_model.get_topics()

# alpha 출력
print("Alpha values: ", alpha)

# beta 출력 (첫번째 주제에서의 분포)
print("Beta (첫번째 주제): ", beta[0])

# beta 행렬의 shape
print("Beta matrix shape: ", beta.shape)

Alpha values:  [0.1 0.1 0.1 0.1 0.1 0.1 0.1 0.1 0.1 0.1]
Beta (첫번째 주제):  [5.4180746e-06 5.4180123e-06 9.3111675e-03 4.2938381e-03 5.4181910e-06
 7.6040537e-03 6.4112451e-03 5.4166590e-06 8.5471040e-03 1.5312415e-02
 6.1863991e-03 9.6937660e-03 5.4179400e-06 1.8944804e-03 3.2267473e-03
 5.4180741e-06 6.7991030e-04 5.4176207e-06 4.2011566e-04 5.4174793e-06
 5.4177090e-06 6.1254716e-03 5.4171605e-06 8.0781057e-03 1.6494627e-03
 3.1717974e-04 1.2863618e-03 2.5107518e-03 5.4171142e-06 5.4165048e-06
 5.1153018e-03 5.4178217e-06 1.6729976e-03 2.2886570e-03 2.0166410e-03
 1.1440256e-03 5.4172747e-06 5.4164302e-06 1.7017663e-03 5.4174570e-06
 5.4176617e-06 1.4267621e-03 5.4175293e-06 5.4173120e-06 5.4176389e-06
 5.4169518e-06 5.4172533e-06 5.4188840e-06 2.4787555e-02 5.3689885e-03
 2.9849424e-03 5.6372867e-03 5.4173006e-06 5.4178513e-06 5.4180359e-06
 5.6686954e-06 5.4162888e-06 4.0266700e-03 2.1088612e-03 5.4176130e-06
 5.4176567e-06 5.4189522e-06 5.4174948e-06 3.9685513e-03 5.4176367e-06
 4.3

>  여기서 beta 행렬값은 첫번째 문서안에서 각각의 단어가 나타날 확률값이 계산되어있음을 알 수 있습니다.

토픽의 수 num_topics 값을 2,3,4,5,6,...,19,20으로 변화시켜가면서 UMass Coherence와 코사인 유사도 값을 구한 후

이들 지표를 이용하여 적절한 토픽의 수를 선택하겠습니다.

* UMass Coherence 값은 LDA 모형에서 출력되는 값을 사용

* 코사인 유사도 값은 문제3에서 작성한 함수를 이용하여 생성

In [33]:
import re
import nltk
from sklearn.datasets import fetch_20newsgroups
from nltk.corpus import stopwords
from nltk.stem import WordNetLemmatizer
from gensim import corpora
from gensim.models.ldamodel import LdaModel
from gensim.models import CoherenceModel
from sklearn.metrics.pairwise import cosine_similarity
import numpy as np

In [34]:
# 순회할 토픽 번호 저장
num_topics_list = list(range(2, 21))

# coherence와 코사인 유사도 저장 위치
coherence_values = []
cosine_similarity_values = []

for num_topics in num_topics_list:
    # LDA model
    lda_model = LdaModel(
        corpus=corpus,
        id2word=dictionary,
        num_topics=num_topics,
        chunksize=200,
        passes=20,
        iterations=400,
        eval_every=10
    )

    # UMass Coherence 계산
    coherence_model_lda = CoherenceModel(model=lda_model, corpus=corpus, dictionary=dictionary, coherence='u_mass')
    coherence_lda = coherence_model_lda.get_coherence()
    coherence_values.append(coherence_lda)

    # 주제-단어 분포 행렬을 가져오기
    topics_matrix = lda_model.get_topics()

    # 코사인 유사도 계산
    cosine_sim = cos(topics_matrix)

    # 주제 간의 평균 코사인 유사도
    upper_triangle_indices = np.triu_indices_from(cosine_sim, k=1)
    mean_cosine_similarity = cosine_sim[upper_triangle_indices].mean()
    cosine_similarity_values.append(mean_cosine_similarity)

    print(f'Num Topics: {num_topics}, Coherence: {coherence_lda}, Cosine Similarity: {mean_cosine_similarity}')

Num Topics: 2, Coherence: -1.3653992756197844, Cosine Similarity: 0.5031460523605347
Num Topics: 3, Coherence: -1.289129605012338, Cosine Similarity: 0.5277482867240906
Num Topics: 4, Coherence: -1.3820773383392093, Cosine Similarity: 0.43198397755622864
Num Topics: 5, Coherence: -1.7073096604522036, Cosine Similarity: 0.2686788737773895
Num Topics: 6, Coherence: -1.6223341672428946, Cosine Similarity: 0.19702482223510742
Num Topics: 7, Coherence: -1.8654255740894168, Cosine Similarity: 0.17964774370193481
Num Topics: 8, Coherence: -1.953861051720078, Cosine Similarity: 0.13898904621601105
Num Topics: 9, Coherence: -1.7282586629061472, Cosine Similarity: 0.19966882467269897
Num Topics: 10, Coherence: -1.7371156358261615, Cosine Similarity: 0.16489125788211823
Num Topics: 11, Coherence: -2.076726451206965, Cosine Similarity: 0.146650031208992
Num Topics: 12, Coherence: -1.9393934017827288, Cosine Similarity: 0.10383957624435425
Num Topics: 13, Coherence: -1.7513637860125741, Cosine Simi

**위에 결과를 해석하여 각 문서의 유사도가 적당히 낮으면서 문서내에 일관성이 높은 토픽수인 5로 잡습니다**
> coherence가 -1.4919로 주변의 값보다 상대적으로 크면서 cosine유사도는 0.3으로 상대적으로 낮습니다 정확히 말하면 분할되는 문서수가 많아질수록 유사도는 당연히
감소하기에 coherence가 큰 값중에서 cosine 유사도가 적당히 낮은값을 택해야합니다.

In [35]:
# LDA 모델 생성
num_topics = 5
lda_model = LdaModel(
    corpus=corpus,
    id2word=dictionary,
    num_topics=num_topics,
    chunksize=200,
    passes=20,
    iterations=400,
    eval_every=10
)

# 각 토픽의 상위 단어 출력
for idx, topic in lda_model.print_topics(num_words=10):
    print(f"Topic {idx + 1}:")
    print(topic)
    print()

# 토픽의 의미 해석
topics = lda_model.show_topics(formatted=False, num_words=10)

topic_words = [[word for word, _ in topic[1]] for topic in topics]

# 토픽 해석
for i, words in enumerate(topic_words):
    print(f"Topic {i + 1} interpretation:")
    print(words)
    print()

Topic 1:
0.052*"''" + 0.040*"space" + 0.017*"'" + 0.016*"file" + 0.013*"launch" + 0.013*"nasa" + 0.012*"e" + 0.012*"orbit" + 0.011*"system" + 0.010*"moon"

Topic 2:
0.025*"''" + 0.021*"n't" + 0.018*"would" + 0.017*"'s" + 0.014*"gun" + 0.011*"get" + 0.011*"people" + 0.010*"write" + 0.010*"one" + 0.009*"article"

Topic 3:
0.029*"new" + 0.029*"sale" + 0.028*"university" + 0.024*"nntp-posting-host" + 0.020*"distribution" + 0.018*"please" + 0.018*"offer" + 0.016*"sell" + 0.015*"_" + 0.014*"include"

Topic 4:
0.035*"drive" + 0.022*"use" + 0.018*"card" + 0.016*"system" + 0.012*"get" + 0.012*"disk" + 0.011*"scsi" + 0.011*"controller" + 0.010*"''" + 0.010*"mb"

Topic 5:
0.030*"'s" + 0.019*"n't" + 0.017*"year" + 0.017*"game" + 0.014*"write" + 0.014*"good" + 0.013*"article" + 0.013*"win" + 0.012*"team" + 0.011*"get"

Topic 1 interpretation:
["''", 'space', "'", 'file', 'launch', 'nasa', 'e', 'orbit', 'system', 'moon']

Topic 2 interpretation:
["''", "n't", 'would', "'s", 'gun', 'get', 'people', '



**각 토픽의 상위 단어를 통해 주제를 추정하기**



- 1번 토픽은 `game`과 `win` `run` 을보아 토픽은 스포츠와 관련된 주제인 것으로 추정 해 볼 수 있습니다.
- 2번 토픽은  `gun`, `people`, `use` 등의 단어들이 포함되어 있어 총기 사용과 관련된 토론이나 논의가 포함된 것으로 볼 수 있습니다.
- 3번 토픽은  `sale` `new` 을 보아 판매와 관련한 주제인 것으로 추정 해 볼 수 있습니다.
- 4번 토픽은 `space` `launch` `nasa` `orbit` 등을보아 우주의 관한 주제임을 추정해 볼 수 있습니다.
- 5번 토픽은 `controller`, `card`, `system` 등을 통해 컴퓨터 하드웨어와 관련한 내용임을 추론 해 볼 수 있습니다.